In [1]:
import pandas as pd 
from datetime import datetime 
from datetime import date
import matplotlib.pyplot as plt
import numpy as np
import pandas as pd
from keras.models import Sequential
from keras.layers import LSTM, Dense
from sklearn.model_selection import train_test_split
from sklearn.preprocessing import MinMaxScaler,StandardScaler
from keras.callbacks import ModelCheckpoint
import tensorflow as tf

In [2]:
merged = pd.read_csv(r'../data/long_merge.csv')

In [3]:
zones = [69, 68,67, 66,65, 64, 42,41,40,39,38,37,36]
rtus = [1]
cols = []

for zone in zones:
        for column in merged.columns:
            if f"zone_0{zone}" in column and 'co2' not in column and "hw_valve" not in column and "cooling_sp" not in column and "heating_sp" not in column:
                cols.append(column)

for zone in zones:
        for column in merged.columns:
              if f"zone_0{zone}" in column: 
                if "cooling_sp" in column or "heating_sp" in column:
                  cols.append(column)
# for rtu in rtus:
#     for column in merged.columns:
#         if f"rtu_00{rtu}_fltrd_sa" in column:
#                 cols.append(column)
cols =['date'] + cols + ['air_temp_set_1',
 'air_temp_set_2',
 'dew_point_temperature_set_1d',
 'relative_humidity_set_1',
 'solar_radiation_set_1']
input_dataset = merged[cols]

In [4]:
input_dataset['date'] = pd.to_datetime(input_dataset['date'], format = "%Y-%m-%d %H:%M:%S")
df_filtered = input_dataset[ (input_dataset.date.dt.date >date(2019, 1, 1)) & (input_dataset.date.dt.date< date(2021, 1, 1))]

if df_filtered.isna().any().any():
    print("There are NA values in the DataFrame columns.")

C:\Users\arbal\AppData\Local\Temp\ipykernel_16740\4293840618.py:1: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  input_dataset['date'] = pd.to_datetime(input_dataset['date'], format = "%Y-%m-%d %H:%M:%S")


There are NA values in the DataFrame columns.


In [5]:
df_filtered

date  zone_069_temp  zone_069_fan_spd  zone_068_temp  \
438785  2019-01-08 20:55:00           70.9               NaN           72.4   
438786  2019-01-08 20:56:00           70.9               NaN           72.4   
438787  2019-01-08 20:57:00           70.9               NaN           72.4   
438788  2019-01-08 20:58:00           70.9               NaN           72.4   
438789  2019-01-08 20:59:00           70.9               NaN           72.4   
...                     ...            ...               ...            ...   
2072148 2020-12-31 23:57:00           68.8              20.0           71.7   
2072149 2020-12-31 23:58:00           68.8              20.0           71.7   
2072150 2020-12-31 23:58:00           68.8              20.0           71.7   
2072151 2020-12-31 23:59:00           68.8              20.0           71.7   
2072152 2020-12-31 23:59:00           68.8              20.0           71.7   

         zone_068_fan_spd  zone_067_temp  zone_067_fan_spd  zone_066_temp  \
438785               20.0           70.2               NaN           70.9   
438786               20.0           70.2               NaN           70.9   
438787               20.0           70.2               NaN           70.9   
438788               20.0           70.2               NaN           70.9   
438789               20.0           70.2               NaN           70.9   
...                   ...            ...               ...            ...   
2072148              20.0           70.4              20.0           68.6   
2072149              20.0           70.4              20.0           68.6   
2072150              20.0           70.4              20.0           68.6   
2072151              20.0           70.4              20.0           68.6   
2072152              20.0           70.4              20.0           68.6   

         zone_066_fan_spd  zone_042_temp  ...  zone_038_heating_sp  \
438785                NaN           72.3  ...                 72.0   
438786                NaN           72.3  ...                 72.0   
438787                NaN           72.3  ...                 72.0   
438788                NaN           72.3  ...                 72.0   
438789                NaN           72.3  ...                 72.0   
...                   ...            ...  ...                  ...   
2072148              35.0           71.4  ...                 71.0   
2072149              35.0           71.4  ...                 71.0   
2072150              35.0           71.4  ...                 71.0   
2072151              35.0           71.4  ...                 71.0   
2072152              35.0           71.4  ...                 71.0   

         zone_037_cooling_sp  zone_037_heating_sp  zone_036_cooling_sp  \
438785                  73.0                 70.0                 75.0   
438786                  73.0                 70.0                 75.0   
438787                  73.0                 70.0                 75.0   
438788                  73.0                 70.0                 75.0   
438789                  73.0                 70.0                 75.0   
...                      ...                  ...                  ...   
2072148                 74.0                 68.0                 74.0   
2072149                 74.0                 68.0                 74.0   
2072150                 74.0                 68.0                 74.0   
2072151                 74.0                 68.0                 74.0   
2072152                 74.0                 68.0                 74.0   

         zone_036_heating_sp  air_temp_set_1  air_temp_set_2  \
438785                  72.0          12.850          12.930   
438786                  72.0          12.850          12.930   
438787                  72.0          12.850          12.930   
438788                  72.0          12.850          12.930   
438789                  72.0          12.850          12.930   
...                      ...       

In [6]:
testdataset_df = df_filtered[(df_filtered.date.dt.date >date(2020, 3, 1)) & (df_filtered.date.dt.date <date(2020,7, 1))]

# traindataset_df = df_filtered[ (df_filtered.date.dt.date >date(2019, 11, 8))]

traindataset_df = df_filtered[(df_filtered.date.dt.date >date(2019, 3, 1)) & (df_filtered.date.dt.date <date(2020, 3, 1)) | (df_filtered.date.dt.date >date(2020, 7, 1)) & (df_filtered.date.dt.date <date(2020, 12, 1))]
testdataset = testdataset_df.drop(columns=["date"]).values
traindataset = traindataset_df.drop(columns=["date"]).values

columns_with_na = traindataset_df.columns[traindataset_df.isna().any()].tolist()
columns_with_na

[]

In [7]:
print(traindataset_df.isna().sum().sum(), testdataset_df.isna().sum().sum())

0 0


In [8]:
len(traindataset), len(testdataset)

(1073512, 391818)

In [9]:
traindataset = traindataset.astype('float32')
testdataset = testdataset.astype('float32')

scaler = StandardScaler()
traindataset = scaler.fit_transform(traindataset)
testdataset = scaler.transform(testdataset)

In [10]:
traindataset.shape

(1073512, 45)

In [11]:
train,test = traindataset,testdataset

def create_dataset(dataset,time_step):
    x = []
    Y = []
    for i in range(len(dataset) - time_step - 1):
        x.append(dataset[i:(i+time_step),:])
        Y.append(dataset[i+time_step,0:23])
    x= np.array(x)
    Y = np.array(Y)
    return x,Y
time_step = 30
X_train, y_train = create_dataset(train, time_step)
X_test, y_test = create_dataset(test, time_step)



In [12]:
X_train.shape, y_train.shape

((1073481, 30, 45), (1073481, 23))

In [13]:

model = Sequential()
model.add(LSTM(units=50, return_sequences=True, input_shape=(X_train.shape[1], X_train.shape[2])))
model.add(LSTM(units=50, return_sequences=True))
model.add(LSTM(units=30))
model.add(Dense(units=y_train.shape[1]))

model.compile(optimizer='adam', loss='mean_squared_error')

checkpoint_path = "lstm_vav_01.tf"
checkpoint_callback = ModelCheckpoint(filepath=checkpoint_path, monitor='val_loss', verbose=1, save_best_only=True, mode='min')
model.fit(X_train, y_train, validation_data=(X_test, y_test), epochs=5, batch_size=128, verbose=1, callbacks=[checkpoint_callback])

Epoch 1/5
8387/8387 [==============================] - ETA: 0s - loss: 0.0178
Epoch 1: val_loss improved from inf to 0.42313, saving model to lstm_vav_01.tf
INFO:tensorflow:Assets written to: lstm_vav_01.tf\assets


INFO:tensorflow:Assets written to: lstm_vav_01.tf\assets


8387/8387 [==============================] - 307s 36ms/step - loss: 0.0178 - val_loss: 0.4231
Epoch 2/5
8387/8387 [==============================] - ETA: 0s - loss: 0.0032
Epoch 2: val_loss improved from 0.42313 to 0.40364, saving model to lstm_vav_01.tf
INFO:tensorflow:Assets written to: lstm_vav_01.tf\assets


INFO:tensorflow:Assets written to: lstm_vav_01.tf\assets


8387/8387 [==============================] - 274s 33ms/step - loss: 0.0032 - val_loss: 0.4036
Epoch 3/5
 259/8387 [..............................] - ETA: 4:02 - loss: 0.0028

KeyboardInterrupt: 

In [14]:
model.load_weights(checkpoint_path)

In [15]:
test_predict1 = model.predict(X_test)

12244/12244 [==============================] - 58s 5ms/step


In [16]:
traindataset_df.columns

Index(['date', 'zone_069_temp', 'zone_069_fan_spd', 'zone_068_temp',
       'zone_068_fan_spd', 'zone_067_temp', 'zone_067_fan_spd',
       'zone_066_temp', 'zone_066_fan_spd', 'zone_042_temp',
       'zone_042_fan_spd', 'zone_041_temp', 'zone_041_fan_spd',
       'zone_040_temp', 'zone_040_fan_spd', 'zone_039_temp',
       'zone_039_fan_spd', 'zone_038_temp', 'zone_038_fan_spd',
       'zone_037_temp', 'zone_037_fan_spd', 'zone_036_temp',
       'zone_036_fan_spd', 'zone_069_cooling_sp', 'zone_069_heating_sp',
       'zone_067_cooling_sp', 'zone_067_heating_sp', 'zone_066_cooling_sp',
       'zone_066_heating_sp', 'zone_042_cooling_sp', 'zone_042_heating_sp',
       'zone_041_cooling_sp', 'zone_041_heating_sp', 'zone_039_cooling_sp',
       'zone_039_heating_sp', 'zone_038_cooling_sp', 'zone_038_heating_sp',
       'zone_037_cooling_sp', 'zone_037_heating_sp', 'zone_036_cooling_sp',
       'zone_036_heating_sp', 'air_temp_set_1', 'air_temp_set_2',
       'dew_point_temperature_set_1d'

In [37]:
%matplotlib qt
plt.figure()
var = 1
plt.plot(y_test[:,var], label='Original Testing Data', color='blue')
plt.plot(test_predict1[:,var], label='Predicted Testing Data', color='red',alpha=0.8)
anomalies = np.where(abs(test_predict1[:,var] - y_test[:,var]) > 0.38)
plt.scatter(anomalies,test_predict1[anomalies,var], color='black',marker ="o",s=100 )


plt.title('Testing Data - Predicted vs Actual')
plt.xlabel('Time')
plt.ylabel('Value')
plt.legend()
plt.show()

In [18]:
from sklearn.mixture import GaussianMixture
import numpy as np
import matplotlib.pyplot as plt
from sklearn.decomposition import PCA


# Generating random data for demonstration
np.random.seed(0)
X =  test_predict1 - y_test


pca = PCA(n_components=2)
X = pca.fit_transform(X)


# Creating the GMM instance with desired number of clusters
gmm = GaussianMixture(n_components=2)

# Fitting the model to the data
gmm.fit(X)

# Getting the cluster labels
labels = gmm.predict(X)

# Plotting the data points with colors representing different clusters
plt.scatter(X[:, 0], X[:, 1], c=labels, cmap='viridis', alpha=0.5)
plt.title('GMM Clustering')
plt.xlabel('Feature 1')
plt.ylabel('Feature 2')
plt.show()


In [ ]:
from sklearn.cluster import KMeans
import numpy as np
import matplotlib.pyplot as plt
from sklearn.decomposition import PCA

# Generating random data for demonstration
np.random.seed(0)
X = (test_predict1 - y_test)

k = 6

kmeans = KMeans(n_clusters=k)

kmeans.fit(X)


pca = PCA(n_components=2)
X = pca.fit_transform(X)



# Getting the cluster centers and labels
centroids = kmeans.cluster_centers_
centroids = pca.transform(centroids)
labels = kmeans.labels_

# Plotting the data points and cluster centers
plt.scatter(X[:, 0], X[:, 1], c=labels, cmap='viridis', alpha=0.5)
plt.scatter(centroids[:, 0], centroids[:, 1], marker='x', c='red', s=200, linewidths=2)
plt.title('KMeans Clustering')
plt.xlabel('Feature 1')
plt.ylabel('Feature 2')
plt.show()


In [19]:
k = 60
X= test_predict1 - y_test
processed_data = []
feat_df = pd.DataFrame(columns=["mean","std",])
for i in range(0,len(X), 60):
    mean = X[i:i+k].mean(axis = 0)
    std = X[i:i+k].std(axis = 0)
    max = X[i:i+k].max(axis = 0)
    min = X[i:i+k].min(axis = 0)
    iqr = np.percentile(X[i:i+k], 75, axis=0) - np.percentile(X[i:i+k], 25,axis=0)
    data = np.concatenate([mean, std, max, min, iqr])
    processed_data.append([data])
processed_data = np.concatenate(processed_data,axis=0) 

In [ ]:
X = processed_data

kmeans = KMeans(n_clusters=3, algorithm='elkan', max_iter=1000, n_init = 5)

kmeans.fit(X)

pca = PCA(n_components=2)
X = pca.fit_transform(X)


# Getting the cluster centers and labels
centroids = kmeans.cluster_centers_
centroids = pca.transform(centroids)
labels = kmeans.labels_

# Plotting the data points and cluster centers
plt.scatter(X[:, 0], X[:, 1], c=labels, cmap='viridis', alpha=0.5)
plt.scatter(centroids[:, 0], centroids[:, 1], marker='x', c='red', s=200, linewidths=2)
plt.title('KMeans Clustering')
plt.xlabel('Feature 1')
plt.ylabel('Feature 2')
plt.show()


In [21]:
from sklearn.mixture import GaussianMixture
import numpy as np
import matplotlib.pyplot as plt
from sklearn.decomposition import PCA

# Generating random data for demonstration
np.random.seed(0)
X = processed_data

# Creating the GMM instance with desired number of clusters
gmm = GaussianMixture(n_components=2, init_params='k-means++')

# Fitting the model to the data
gmm.fit(X)
labels = gmm.predict(X)


pca = PCA(n_components=2)
X = pca.fit_transform(X)


# Getting the cluster labels

# Plotting the data points with colors representing different clusters
plt.scatter(X[:, 0], X[:, 1], c=labels, cmap='viridis', alpha=0.5)
plt.title('GMM Clustering')
plt.xlabel('Feature 1')
plt.ylabel('Feature 2')
plt.show()



In [38]:
from sklearn.cluster import KMeans
import numpy as np
import matplotlib.pyplot as plt
# Generating random data for demonstration
np.random.seed(0)
X = test_predict1 - y_test 

kmeans = KMeans(n_clusters=2)

kmeans.fit(X)


pca = PCA(n_components=2)
X = pca.fit_transform(X)



# Getting the cluster centers and labels
centroids = kmeans.cluster_centers_
centroids = pca.transform(centroids)
labels = kmeans.labels_

# Plotting the data points and cluster centers
plt.figure()
plt.scatter(X[:, 0], X[:, 1], c=labels, cmap='viridis', alpha=0.5)
plt.scatter(centroids[:, 0], centroids[:, 1], marker='x', c='red', s=200, linewidths=2)
plt.text(centroids[0,0], centroids[0,1], 'Normal', fontsize=12, color='red')
plt.text(centroids[1,0], centroids[1,1], 'Anomaly', fontsize=12, color='red')
plt.title('KMeans Clustering')
plt.xlabel('Feature 1')
plt.ylabel('Feature 2')
plt.show()


In [29]:
sum(labels==0)

329810